In [1]:
import torch
import torch.nn as nn
import torch.optim as optim
import torchvision.datasets as dsets
import torchvision.transforms as transforms
from torch.utils.data import DataLoader
import torch.optim as optim
import matplotlib.pyplot as plt
import os

In [2]:
print(torch.cuda.is_available())
print(torch.version.cuda)
print(torch.__version__)

True
12.4
2.4.1+cu124


In [3]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

Using device: cuda


In [4]:
batchSize = 32
imageSize = 32
latentDim = 128
numberOfEpochs = 100
learningRateGenerator = 0.0001
learningRateDiscriminator = 0.0001

In [5]:
transform = transforms.Compose([
    transforms.Resize(imageSize),
    transforms.ToTensor(),
    transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))
])
dataset = dsets.CIFAR10(root = './data', download = True, transform = transform)
dataloader = DataLoader(dataset, batch_size = 64, shuffle = True)

Files already downloaded and verified


In [6]:
class Generator(nn.Module):
    def __init__(self):
        super(Generator, self).__init__()
        self.model = nn.Sequential(
            nn.Linear(latentDim, 256), 
            nn.LeakyReLU(0.2, inplace = True), 
            nn.BatchNorm1d(256), 
            nn.Linear(256, 512),
            nn.LeakyReLU(0.2, inplace = True), 
            nn.BatchNorm1d(512), 
            nn.Linear(512, 1024), 
            nn.LeakyReLU(0.2, inplace = True), 
            nn.BatchNorm1d(1024), 
            nn.Linear(1024, 3 * imageSize * imageSize), 
            nn.Tanh()
        )
    
    def forward(self, input):
        image = self.model(input)
        image = image.view(image.size(0), 3, imageSize, imageSize)
        return image

In [7]:
class Discriminator(nn.Module):
    def __init__(self):
        super(Discriminator, self).__init__()
        self.model = nn.Sequential(
            nn.Linear(3 * imageSize * imageSize, 1024), 
            nn.LeakyReLU(0.2, inplace = True), 
            nn.Dropout(0.3), 
            nn.Linear(1024, 512), 
            nn.LeakyReLU(0.2, inplace = True), 
            nn.Dropout(0.3), 
            nn.Linear(512, 256), 
            nn.LeakyReLU(0.2, inplace = True), 
            nn.Linear(256, 1), 
            nn.Sigmoid()
        )
    
    def forward(self, input):
        return self.model(input.view(-1, 3 * 32 * 32))

In [8]:
criterion = nn.BCELoss()
optimizerDiscriminator = optim.Adam(Discriminator().parameters(), lr = learningRateDiscriminator, betas = (0.5, 0.999))
optimizerGenerator = optim.Adam(Generator().parameters(), lr = learningRateGenerator, betas = (0.5, 0.999))

SchedulerGenerator = optim.lr_scheduler.ReduceLROnPlateau(optimizerGenerator, mode = 'min', factor = 0.5, patience = 5)
SchedulerDiscriminator = optim.lr_scheduler.ReduceLROnPlateau(optimizerDiscriminator, mode = 'min', factor = 0.5, patience = 5)

In [9]:
saveDir = os.path.join(os.getcwd(), "GAN_Images")

if not os.path.exists(saveDir):
    os.makedirs(saveDir)

saveDir


'd:\\Finally, A study Folder\\Thapar Summer School on Machine Learning and Deep Learning\\GAN\\VanillaGAN\\GAN_Images'

In [10]:
discriminator = Discriminator().to(device)
generator = Generator().to(device)

for epoch in range(numberOfEpochs):
    for i, data in enumerate(dataloader):
        images, _ = data
        realImages = images.to(device)

        realLabels = torch.ones(realImages.size(0)).to(device)
        fakeLabels = torch.zeros(realImages.size(0)).to(device)

        #Train Discriminator
        optimizerDiscriminator.zero_grad()
        outputReal = discriminator(realImages.view(realImages.size(0), -1)).view(-1)
        realLoss = criterion(outputReal, realLabels)
        realLoss.backward()

        noise = torch.randn(realImages.size(0), latentDim, device=device)
        fakeImages = generator(noise)
        outputFake = discriminator(fakeImages.detach().view(fakeImages.size(0), -1)).view(-1)
        fakeLoss = criterion(outputFake, fakeLabels)
        fakeLoss.backward()
        optimizerDiscriminator.step()

        #Train Generator
        optimizerGenerator.zero_grad()
        outputGenerated = discriminator(fakeImages.view(fakeImages.size(0), -1)).view(-1)
        generatorLoss = criterion(outputGenerated, realLabels)
        generatorLoss.backward()
        optimizerGenerator.step()

        print(f"Epoch [{epoch + 1}/{numberOfEpochs}]  Loss D: {realLoss.item() + fakeLoss.item():.4f}, Loss G: {generatorLoss.item():.4f}")

    if epoch % 10 == 0:
        plt.figure(figsize=(10, 10))
        with torch.no_grad():
            z = torch.randn(25, latentDim).to(device)
            fakeImages = generator(z).detach().cpu()
            for j in range(25):
                plt.subplot(5, 5, j + 1)
                plt.imshow((fakeImages[j].permute(1, 2, 0).numpy() * 0.5) + 0.5)
                plt.axis('off')

        plt.savefig(os.path.join(saveDir, f'epoch_{epoch + 1}.png'))
        plt.show()
        plt.close()

print("Training finished.")


Epoch [1/100]  Loss D: 1.3888, Loss G: 0.6614
Epoch [1/100]  Loss D: 1.3856, Loss G: 0.6612
Epoch [1/100]  Loss D: 1.3861, Loss G: 0.6602
Epoch [1/100]  Loss D: 1.3888, Loss G: 0.6617
Epoch [1/100]  Loss D: 1.3863, Loss G: 0.6609
Epoch [1/100]  Loss D: 1.3889, Loss G: 0.6639
Epoch [1/100]  Loss D: 1.3888, Loss G: 0.6616
Epoch [1/100]  Loss D: 1.3894, Loss G: 0.6602
Epoch [1/100]  Loss D: 1.3874, Loss G: 0.6627
Epoch [1/100]  Loss D: 1.3871, Loss G: 0.6622
Epoch [1/100]  Loss D: 1.3886, Loss G: 0.6619
Epoch [1/100]  Loss D: 1.3838, Loss G: 0.6627
Epoch [1/100]  Loss D: 1.3865, Loss G: 0.6626
Epoch [1/100]  Loss D: 1.3840, Loss G: 0.6595
Epoch [1/100]  Loss D: 1.3844, Loss G: 0.6611
Epoch [1/100]  Loss D: 1.3875, Loss G: 0.6604
Epoch [1/100]  Loss D: 1.3888, Loss G: 0.6617
Epoch [1/100]  Loss D: 1.3839, Loss G: 0.6625
Epoch [1/100]  Loss D: 1.3832, Loss G: 0.6604
Epoch [1/100]  Loss D: 1.3847, Loss G: 0.6622
Epoch [1/100]  Loss D: 1.3869, Loss G: 0.6615
Epoch [1/100]  Loss D: 1.3838, Los